In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
%pip install --quiet --upgrade diffusers transformers accelerate invisible_watermark mediapy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 20.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.4/261.4 kB 27.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 49.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 76.7 MB/s eta 0:00:00


In [3]:
use_refiner = False
use_latent_consistency = True

In [4]:
import mediapy as media
import random
import sys
import torch

from diffusers import DiffusionPipeline, LCMScheduler

pipe = DiffusionPipeline.from_pretrained(
    "stabilityai/stable-diffusion-xl-base-1.0",
    torch_dtype=torch.float16,
    use_safetensors=True,
    variant="fp16",
    )

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

model_index.json:   0%|          | 0.00/609 [00:00<?, ?B/s]

Fetching 19 files:   0%|          | 0/19 [00:00<?, ?it/s]

scheduler/scheduler_config.json:   0%|          | 0.00/479 [00:00<?, ?B/s]

...

vae/config.json:   0%|          | 0.00/642 [00:00<?, ?B/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/5.14G [00:00<?, ?B/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/167M [00:00<?, ?B/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/167M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [5]:
if use_refiner:
  refiner = DiffusionPipeline.from_pretrained(
      "stabilityai/stable-diffusion-xl-refiner-1.0",
      text_encoder_2=pipe.text_encoder_2,
      vae=pipe.vae,
      torch_dtype=torch.float16,
      use_safetensors=True,
      variant="fp16",
  )

  refiner = refiner.to("cuda")

  pipe.enable_model_cpu_offload()
else:
  pipe = pipe.to("cuda")

In [6]:
if use_latent_consistency:
  pipe.load_lora_weights("latent-consistency/lcm-lora-sdxl")
  pipe.scheduler = LCMScheduler.from_config(pipe.scheduler.config)

  guidance_scale = 1
  num_inference_steps = 4
else:
  guidance_scale = 5
  num_inference_steps = 50

pytorch_lora_weights.safetensors:   0%|          | 0.00/394M [00:00<?, ?B/s]

The config attributes {'skip_prk_steps': True} were passed to LCMScheduler, but are not expected and will be ignored. Please verify your scheduler_config.json configuration file.


In [7]:
!mkdir ./fake

In [13]:
import pandas as pd
from PIL import Image

# Load the CSV file

# Specify the directory where images will be saved
output_folder = './fake/'

In [ ]:
negative_prompt = "undamaged, pristine, perfect condition, showroom new, no scratches, no dents, no wear and tear, smooth hood, flawless, unrealistic deformations, exaggerated damage, overly distorted structures"
prompts = [
    "crack.",
    "shattered glass.",
    "broken lamp.",
    "flat tire.",
    "dented bumper.",
    "scratched paint.",
    "leaking oil.",
    "smashed windshield.",
    "rusty body.",
    "missing side mirror.",
    "burned-out headlights.",
    "dent in the door.",
    "engine smoke.",
    "broken side mirror.",
    "deflated tire.",
    "fender bender damage.",
    "keyed paint.",
    "torn upholstery.",
    "fallen-off license plate.",
]

# Iterate over each row in the DataFrame
for row in prompts:
    for i in range (50) :
      seed = random.randint(0, sys.maxsize)
      base_prompt = row

      # Generate 1 image with the modified prompt
      modified_prompt = "A photo of a car has a " + base_prompt
      print("Used prompt:", modified_prompt)  # Print the used prompt
      images = pipe(
              prompt = modified_prompt,
              negative_prompt = negative_prompt,
              guidance_scale = guidance_scale,
              num_inference_steps = num_inference_steps,
              output_type = "latent" if use_refiner else "pil",
              generator = torch.Generator("cuda").manual_seed(seed),
              ).images

      if use_refiner:
        images = refiner(
            prompt = modified_prompt,
            negative_prompt = negative_prompt,
            image = images,
            ).images

      image = images[0]

      # Save the image
      image_path = f"{output_folder}image_{seed}.png"
      image.save(image_path)

    for j in range (150) :
      seed = random.randint(0, sys.maxsize)
      base_prompt = row

      # Generate 1 image with the modified prompt
      modified_prompt = "A close view of a car that has a " + base_prompt
      print("Used prompt:", modified_prompt)  # Print the used prompt
      images = pipe(
              prompt = modified_prompt,
              negative_prompt = negative_prompt,
              guidance_scale = guidance_scale,
              num_inference_steps = num_inference_steps,
              output_type = "latent" if use_refiner else "pil",
              generator = torch.Generator("cuda").manual_seed(seed),
              ).images

      if use_refiner:
        images = refiner(
            prompt = modified_prompt,
            negative_prompt = negative_prompt,
            image = images,
            ).images

      image = images[0]

      # Save the image
      image_path = f"{output_folder}image_{seed}.png"
      image.save(image_path)

print("Images generated and saved.")


Used prompt: A photo of a car has a crack.


  0%|          | 0/4 [00:00<?, ?it/s]

Used prompt: A photo of a car has a crack.


  0%|          | 0/4 [00:00<?, ?it/s]

Used prompt: A photo of a car has a crack.


...

  0%|          | 0/4 [00:00<?, ?it/s]

Used prompt: A close view of a car that has a broken lamp.


  0%|          | 0/4 [00:00<?, ?it/s]

Used prompt: A close view of a car that has a broken lamp.


  0%|          | 0/4 [00:00<?, ?it/s]